# Evaluation with Ragas

In [14]:
import sys
import os

sys.path.append(os.path.abspath("../"))

In [19]:
import time

current_timestamp = int(time.time() * 1000)

print(1747978887 > current_timestamp)

False


In [2]:
from psycopg_pool import AsyncConnectionPool
from langgraph.checkpoint.postgres.aio import AsyncPostgresSaver

In [20]:
from app.retrieval.vector_store import vector_store_service
from app.core.database import session_manager, pgvector_session_manager
from app.env import DATABASE_URL
from app.retrieval.chain import chain_service

In [4]:
async def setup_environment():
    await session_manager.initialize()
    vector_store_service.initialize_embedding_model('../data/sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2')
    vector_store_service.initialize_pg_vector()
    chain_service.load_model_collection()
    await pgvector_session_manager.initialize()

    DB_URI = f"postgresql://{DATABASE_URL}?sslmode=disable"
    connection_kwargs = {
        "autocommit": True,
        "prepare_threshold": 0,
    }

    pool = AsyncConnectionPool(conninfo=DB_URI, max_size=20, kwargs=connection_kwargs)
    await pool.__aenter__()  # manually enter the async context

    checkpointer = AsyncPostgresSaver(pool)
    await checkpointer.setup()
    chain_service.set_checkpointer(checkpointer)

    return pool  # Keep reference to close later

# Run setup once in the notebook
pool = await setup_environment()

Initialize embedding model...
../data/sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2


INFO     2025-05-23 05:26:19,391 sentence_transformers.SentenceTransformer INFO: Use     ]8;id=912049;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\sentence_transformers\SentenceTransformer.py\SentenceTransformer.py]8;;\:]8;id=107914;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\sentence_transformers\SentenceTransformer.py#210\210]8;;\
         pytorch device_name: cpu                                                                                  

INFO     2025-05-23 05:26:19,396 sentence_transformers.SentenceTransformer INFO: Load    ]8;id=574367;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\sentence_transformers\SentenceTransformer.py\SentenceTransformer.py]8;;\:]8;id=504695;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\sentence_transformers\SentenceTransformer.py#218\218]8;;\
         pretrained SentenceTransformer:                                                                           
         ../data/sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2                                       

Successfully initialize embedding model


INFO     2025-05-23 05:26:21,187 app.retrieval.vector_store INFO: Initializing PGVector          ]8;id=863124;file://f:\project\chatbot-ta\chatbot-service\app\retrieval\vector_store.py\vector_store.py]8;;\:]8;id=333393;file://f:\project\chatbot-ta\chatbot-service\app\retrieval\vector_store.py#76\76]8;;\

model_path
f:\project\chatbot-ta\chatbot-service\notebooks\test\best_improved_question_classifier.pkl


In [5]:
from ragas.metrics import (
    answer_relevancy,
    faithfulness,
    context_recall,
    context_precision,
    answer_correctness,
    answer_similarity
)
from langchain.schema import HumanMessage, AIMessage, SystemMessage
from langchain.schema.messages import ToolMessage
from app.retrieval.chain import chain_service

import json
from pprint import pprint
from tqdm import tqdm

In [7]:
with open('question.json', 'r', encoding='utf-8') as f:
    question_data = json.load(f)

question_data = question_data[:50]

questions = [item["question"] for item in question_data]
expected_answers = {item["question"]: item["answer"] for item in question_data}

evaluation_data = []
# count = 0

agent = chain_service.create_agent("openai")

for q in questions:
    print(f"Processing question: {q}")
    try:
        result = await agent.ainvoke(
            {
                "messages": [
                    SystemMessage(content=f"User ID atau sender pesan adalah: user-test"), 
                    HumanMessage(content=str(q))
                ],
            }, 
            # {"configurable": {"thread_id": f"testing-{count}"}}
        )

        tool_messages = [
            message for message in result["messages"]
            if isinstance(message, ToolMessage)
        ]

        contexts = [tool_messages[-1].content] if tool_messages else []

        ai_messages = [
            message.content
            for message in result["messages"]
            if isinstance(message, AIMessage) and message.content.strip()
        ]

        answer = (
            ai_messages[-1]
            if ai_messages
            else "Terjadi kesalahan, tidak ada respon dari AI. Tolong hubungi developer."
        )

        ground_truth = expected_answers.get(q, "No expected answer provided")

        evaluation_data.append({
            "question": q,
            "contexts": contexts,
            "response": answer,
            "ground_truth": ground_truth,
        })

        # count += 1

    except Exception as e:
        print(f"Error processing question '{q}': {e}\n")

Processing question: Berikan jadwal perkuliahan di hari Senin


INFO     2025-05-23 05:29:58,345 httpx INFO: HTTP Request: POST                                     ]8;id=201633;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py\_client.py]8;;\:]8;id=427219;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py#1740\1740]8;;\
         https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"                                              

Retrieving information for query: jadwal perkuliahan hari Senin
2025-05-23 05:29:58,365 INFO sqlalchemy.engine.Engine BEGIN (implicit)


INFO     2025-05-23 05:29:58,365 sqlalchemy.engine.Engine INFO: BEGIN (implicit)                       ]8;id=597716;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\sqlalchemy\engine\base.py\base.py]8;;\:]8;id=684678;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\sqlalchemy\engine\base.py#1097\1097]8;;\

2025-05-23 05:29:58,369 INFO sqlalchemy.engine.Engine SELECT collection.id, collection.name, collection.description, collection.is_active, collection.created_at, collection.updated_at 
FROM collection 
WHERE collection.is_active = true 
 LIMIT $1::INTEGER


...

INFO     2025-05-23 05:43:27,977 httpx INFO: HTTP Request: POST                                     ]8;id=657842;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py\_client.py]8;;\:]8;id=640789;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py#1025\1025]8;;\
         https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"                                              

Jumlah dokumen yang dikembalikan: 8
Document file name: 38d7d7a0-1e68-49d9-97cc-63fa2a58626e_280-SK-Rektor-ttg-Pedoman-Penyusunan-Laporan-Tugas-Akhir-Sarjana-Sarjana-Terapan.pdf
Document file name: 38d7d7a0-1e68-49d9-97cc-63fa2a58626e_280-SK-Rektor-ttg-Pedoman-Penyusunan-Laporan-Tugas-Akhir-Sarjana-Sarjana-Terapan.pdf
Document file name: 38d7d7a0-1e68-49d9-97cc-63fa2a58626e_280-SK-Rektor-ttg-Pedoman-Penyusunan-Laporan-Tugas-Akhir-Sarjana-Sarjana-Terapan.pdf
Document file name: 38d7d7a0-1e68-49d9-97cc-63fa2a58626e_280-SK-Rektor-ttg-Pedoman-Penyusunan-Laporan-Tugas-Akhir-Sarjana-Sarjana-Terapan.pdf
Document file name: 38d7d7a0-1e68-49d9-97cc-63fa2a58626e_280-SK-Rektor-ttg-Pedoman-Penyusunan-Laporan-Tugas-Akhir-Sarjana-Sarjana-Terapan.pdf
Document file name: 38d7d7a0-1e68-49d9-97cc-63fa2a58626e_280-SK-Rektor-ttg-Pedoman-Penyusunan-Laporan-Tugas-Akhir-Sarjana-Sarjana-Terapan.pdf
Document file name: 38d7d7a0-1e68-49d9-97cc-63fa2a58626e_280-SK-Rektor-ttg-Pedoman-Penyusunan-Laporan-Tugas-Akhi

INFO     2025-05-23 05:43:28,647 httpx INFO: HTTP Request: POST                                     ]8;id=165624;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py\_client.py]8;;\:]8;id=563850;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py#1740\1740]8;;\
         https://api.openai.com/v1/chat/completions "HTTP/1.1 429 Too Many Requests"                               

INFO     2025-05-23 05:43:28,652 openai._base_client INFO: Retrying request to                 ]8;id=649827;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\openai\_base_client.py\_base_client.py]8;;\:]8;id=838080;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\openai\_base_client.py#1573\1573]8;;\
         /chat/completions in 14.180000 seconds                                                                    

INFO     2025-05-23 05:43:47,475 httpx INFO: HTTP Request: POST                                     ]8;id=304245;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py\_client.py]8;;\:]8;id=687143;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py#1740\1740]8;;\
         https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"                                              

In [8]:
from datasets import Dataset as HFDataset
from ragas import evaluate

In [9]:
ragas_dataset = HFDataset.from_list(evaluation_data)

result = evaluate(
    ragas_dataset,
    metrics=[
        context_precision,
        faithfulness,
        answer_relevancy,
        context_recall,
        answer_correctness,
        answer_similarity
    ]
)

result.to_pandas()

Evaluating:   0%|          | 0/234 [00:00<?, ?it/s]

INFO     2025-05-23 05:43:54,464 httpx INFO: HTTP Request: POST                                     ]8;id=642359;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py\_client.py]8;;\:]8;id=130011;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py#1740\1740]8;;\
         https://api.openai.com/v1/embeddings "HTTP/1.1 200 OK"                                                    

INFO     2025-05-23 05:43:54,561 httpx INFO: HTTP Request: POST                                     ]8;id=375557;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py\_client.py]8;;\:]8;id=279609;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py#1740\1740]8;;\
         https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"                                              

INFO     2025-05-23 05:43:54,578 httpx INFO: HTTP Request: POST                                     ]8;id=295060;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py\_client.py]8;;\:]8;id=604391;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py#1740\1740]8;;\
         https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"                                              

INFO     2025-05-23 05:43:54,606 httpx INFO: HTTP Request: POST                                     ]8;id=552173;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py\_client.py]8;;\:]8;id=664826;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py#1740\1740]8;;\
         https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"                                              

...

INFO     2025-05-23 05:47:59,263 httpx INFO: HTTP Request: POST                                     ]8;id=350908;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py\_client.py]8;;\:]8;id=397555;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py#1740\1740]8;;\
         https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"                                              

Evaluating: 100%|█████████▉| 233/234 [04:10<00:02,  2.66s/it]

INFO     2025-05-23 05:48:18,243 httpx INFO: HTTP Request: POST                                     ]8;id=798422;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py\_client.py]8;;\:]8;id=80266;file://f:\project\chatbot-ta\chatbot-service\.venv\lib\site-packages\httpx\_client.py#1740\1740]8;;\
         https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"                                              

Evaluating: 100%|██████████| 234/234 [04:29<00:00,  1.15s/it]


user_input  \
0            Berikan jadwal perkuliahan di hari Senin   
1   Siapa saja dosen yang ada di departemen teknol...   
2   Siapa saja staff tata usaha yang ada di depart...   
3        Siapa kepala departemen teknologi informasi?   
4   Apa daftar mata kuliah untuk Angkatan 2024 di ...   
5   Berapa jumlah SKS minimal untuk syarat pengaju...   
6              Bagaimana ketentuan konversi SKS MBKM?   
7   Berapa maksimal konversi SKS untuk Prestasi PK...   
8   Dokumen apa saja yang diperlukan untuk pengaju...   
9   Apa hukuman yang didapatkan jika memalsukan do...   
10                                      Apa itu SKEM?   
11  Apakah Olahraga merupakan kegiatan wajib untuk...   
12  Departemen Teknologi Informasi ada di fakultas...   
13  Apa saja kompetensi utama di departemen teknol...   
14   Kapan berdirinya departemen teknologi informasi?   
15         Apa tujuan departemen teknologi informasi?   
16  Apa visi keilmuan departemen teknologi informasi?   
17           Apa visi departemen teknologi informasi?   
18  Departemen teknologi informasi memiliki berapa...   
19  Bagaimana prospek karir lulusan departemen tek...   
20  Apa saja program seleksi di departemen teknolo...   
21  Apa kode mata kuliah untuk Kecerdasan Artifisi...   
22  Adakah informasi mengenai email dari Bapak Har...   
23  Siapa dosen dengan lulusan termuda di departem...   
24  Di jadwal mata kuliah, di ruang kelas mana mat...   
25  Siapa dosen yang merupakan lulusan dari Kumamo...   
26  Terdapat berapa kelas untuk matakuliah Struktu...   
27  Matakuliah apa yang diajarkan di kelas TW2-703...   
28  Apakah terdapat mata kuliah yang diajarkan di ...   
29  Apakah terdapat informasi mengenai beasiswa ya...   
30  Adakah informasi course yang diadakan oleh Udemy?   
31  Dimana saya bisa mendapatkan informasi untuk m...   
32  Bagaimana cara mendapatkan surat permohonan pe...   
33                             Apa itu event ARA 6.0?   
34       Apa saja rangkaian acara dari event ARA 6.0?   
35  Siapa saja peserta yang dapat mengikuti event ...   
36  Apakah terdapat pengumuman mengenai pengisian ...   
37  Bagaimana format penulisan proposal tugas/proy...   
38  Untuk tugas/proyek akhir, penulisan daftar pus...   

                                   retrieved_contexts  \
0   [("Source: {'jam': '07.00-07.55', 'hari': 'Sen...   
1   [("Source: {'source': 'https://www.its.ac.id/i...   
2   [("Source: {'npp': '2001202442145', 'name': 'h...   
3                                                  []   
4   [("Source: {'name': 'Daftar MK Dibuka Genap 24...   
5   [('Source: {\'name\': \'MBKM-Departemen-Teknol...   
6   [('Source: {\'name\': \'MBKM-Departemen-Teknol...   
7   [("Source: {'name': 'MBKM-Departemen-Teknologi...   
8   [("Source: {'name': 'MBKM-Departemen-Teknologi...   
9   [("Source: {'name': 'MBKM-Departemen-Teknologi...   
10  [("Source: {'source': 'https://www.its.ac.id/i...   
11  [("Source: {'name': 'SKEM-ITS_24-Feb-2021.pdf'...   
12                                                 []   
13  [('Source: {\'source\': \'https://www.its.ac.i...   
14  [("Source: {'source': 'https://www.its.ac.id/i...   
15  [("Source: {'source': 'https://www.its.ac.id/i...   
16  [("Source: {'source': 'https://www.its.ac.id/i...   
17  [('Source: {\'source\': \'https://www.its.ac.i...   
18  [("Source: {'source': 'https://www.its.ac.id/i...   
19  [('Source: {\'source\': \'https://www.its.ac.i...   
20  [("Source: {'source': 'https://www.its.ac.id/i...   
21  [("Source: {'name': 'Daftar MK Dibuka Genap 24...   
22  [("Source: {'nip': '19650518 199203 1 003', 'n...   
23  [("Source: {'source': 'https://www.its.ac.id/i...   
24  [("Source: {'jam': '07.00-07.55', 'hari': 'Sen...   
25  [("Source: {'nip': '19840518201404 1 001', 'na...   
26  [("Source: {'jam': '13.30-14.20', 'hari': 'Sen...   
27  [("Source: {'jam': '07.00-07.55', 'hari': 'Sen...   
28  [("Source: {'jam': '13.30-14.20', 'hari': 'Sen...   
29  [[OpportunitiesReadModel(title='Djarum Beasisw..

In [10]:
df = result.to_pandas()
average_scores = df.mean(numeric_only=True)

print("\nRata-rata setiap metrik:")
print(average_scores)


Rata-rata setiap metrik:
context_precision      0.789474
faithfulness           0.734830
answer_relevancy       0.749831
context_recall         0.672169
answer_correctness     0.538594
semantic_similarity    0.884651
dtype: float64


In [13]:
result.to_pandas()

user_input  \
0            Berikan jadwal perkuliahan di hari Senin   
1   Siapa saja dosen yang ada di departemen teknol...   
2   Siapa saja staff tata usaha yang ada di depart...   
3        Siapa kepala departemen teknologi informasi?   
4   Apa daftar mata kuliah untuk Angkatan 2024 di ...   
5   Berapa jumlah SKS minimal untuk syarat pengaju...   
6              Bagaimana ketentuan konversi SKS MBKM?   
7   Berapa maksimal konversi SKS untuk Prestasi PK...   
8   Dokumen apa saja yang diperlukan untuk pengaju...   
9   Apa hukuman yang didapatkan jika memalsukan do...   
10                                      Apa itu SKEM?   
11  Apakah Olahraga merupakan kegiatan wajib untuk...   
12  Departemen Teknologi Informasi ada di fakultas...   
13  Apa saja kompetensi utama di departemen teknol...   
14   Kapan berdirinya departemen teknologi informasi?   
15         Apa tujuan departemen teknologi informasi?   
16  Apa visi keilmuan departemen teknologi informasi?   
17           Apa visi departemen teknologi informasi?   
18  Departemen teknologi informasi memiliki berapa...   
19  Bagaimana prospek karir lulusan departemen tek...   
20  Apa saja program seleksi di departemen teknolo...   
21  Apa kode mata kuliah untuk Kecerdasan Artifisi...   
22  Adakah informasi mengenai email dari Bapak Har...   
23  Siapa dosen dengan lulusan termuda di departem...   
24  Di jadwal mata kuliah, di ruang kelas mana mat...   
25  Siapa dosen yang merupakan lulusan dari Kumamo...   
26  Terdapat berapa kelas untuk matakuliah Struktu...   
27  Matakuliah apa yang diajarkan di kelas TW2-703...   
28  Apakah terdapat mata kuliah yang diajarkan di ...   
29  Apakah terdapat informasi mengenai beasiswa ya...   
30  Adakah informasi course yang diadakan oleh Udemy?   
31  Dimana saya bisa mendapatkan informasi untuk m...   
32  Bagaimana cara mendapatkan surat permohonan pe...   
33                             Apa itu event ARA 6.0?   
34       Apa saja rangkaian acara dari event ARA 6.0?   
35  Siapa saja peserta yang dapat mengikuti event ...   
36  Apakah terdapat pengumuman mengenai pengisian ...   
37  Bagaimana format penulisan proposal tugas/proy...   
38  Untuk tugas/proyek akhir, penulisan daftar pus...   

                                   retrieved_contexts  \
0   [("Source: {'jam': '07.00-07.55', 'hari': 'Sen...   
1   [("Source: {'source': 'https://www.its.ac.id/i...   
2   [("Source: {'npp': '2001202442145', 'name': 'h...   
3                                                  []   
4   [("Source: {'name': 'Daftar MK Dibuka Genap 24...   
5   [('Source: {\'name\': \'MBKM-Departemen-Teknol...   
6   [('Source: {\'name\': \'MBKM-Departemen-Teknol...   
7   [("Source: {'name': 'MBKM-Departemen-Teknologi...   
8   [("Source: {'name': 'MBKM-Departemen-Teknologi...   
9   [("Source: {'name': 'MBKM-Departemen-Teknologi...   
10  [("Source: {'source': 'https://www.its.ac.id/i...   
11  [("Source: {'name': 'SKEM-ITS_24-Feb-2021.pdf'...   
12                                                 []   
13  [('Source: {\'source\': \'https://www.its.ac.i...   
14  [("Source: {'source': 'https://www.its.ac.id/i...   
15  [("Source: {'source': 'https://www.its.ac.id/i...   
16  [("Source: {'source': 'https://www.its.ac.id/i...   
17  [('Source: {\'source\': \'https://www.its.ac.i...   
18  [("Source: {'source': 'https://www.its.ac.id/i...   
19  [('Source: {\'source\': \'https://www.its.ac.i...   
20  [("Source: {'source': 'https://www.its.ac.id/i...   
21  [("Source: {'name': 'Daftar MK Dibuka Genap 24...   
22  [("Source: {'nip': '19650518 199203 1 003', 'n...   
23  [("Source: {'source': 'https://www.its.ac.id/i...   
24  [("Source: {'jam': '07.00-07.55', 'hari': 'Sen...   
25  [("Source: {'nip': '19840518201404 1 001', 'na...   
26  [("Source: {'jam': '13.30-14.20', 'hari': 'Sen...   
27  [("Source: {'jam': '07.00-07.55', 'hari': 'Sen...   
28  [("Source: {'jam': '13.30-14.20', 'hari': 'Sen...   
29  [[OpportunitiesReadModel(title='Djarum Beasisw..

In [11]:
import pandas as pd

In [12]:
df = result.to_pandas()
df.to_csv("evaluation_result.csv", index=False)
df_eval = pd.DataFrame(evaluation_data)
df_eval.to_csv("raw_evaluation_data.csv", index=False)

In [ ]:
search_results = []

for q in questions:
    query = q.lower()
    top_k = await vector_store_service.asimilarity_search_with_score(query, collection_name='administration')

    for idx, (doc, score) in enumerate(top_k, start=1):
        print(f"Hasil {idx}:")
        print(f"   Skor      : {score:.4f}")  
        print(f"   Bab       : {doc.metadata}")
        print(f"   Konten    : {doc.page_content}\n")
        
        search_results.append({
            "question": q,
            "rank": idx,
            "score": float(f"{score:.4f}"),
            "metadata": doc.metadata,
            "content": doc.page_content
        })

Hasil 1:
   Skor      : 0.4872
   Bab       : {'page': 0, 'author': 'Midyanisa Yuniar', 'source': 'F:\\project\\chatbot-ta\\chatbot-service\\data\\uploads\\8430639b-c02a-4a5e-ab93-22787d46d3c9_Daftar Staff Teknologi Informasi.pdf', 'creator': 'Microsoft® Word for Microsoft 365', 'file_id': '8430639b-c02a-4a5e-ab93-22787d46d3c9', 'moddate': '2025-05-06T23:54:03+07:00', 'producer': 'Microsoft® Word for Microsoft 365', 'file_name': '8430639b-c02a-4a5e-ab93-22787d46d3c9_Daftar Staff Teknologi Informasi.pdf', 'page_label': '1', 'start_index': 0, 'total_pages': 1, 'creationdate': '2025-05-06T23:54:03+07:00'}
   Konten    : Daftar Staff Teknologi Informasi 
Nama Staf :  Khairun Nasihin, S.ST. 
NPP :  1994201721442 
Fungsi :  Kepala Sub Bagian Tata Usaha 
Email :  khairun@its.ac.id 
 
Nama Staf : Lila Ambarwati, S.Pd. 
NPP : 1994201722465 
Fungsi :  Pengelola Keuangan 
Email :  lilambar@its.ac.id 
 
Nama Staf :  Jihan Fadhilah, S.M. 
NPP :  2001202442145 
Fungsi :   Administrasi Akademik Prodi

In [ ]:
df_results = pd.DataFrame(search_results)
df_results.to_csv("similarity_search_results.csv", index=False)

In [ ]:
await session_manager.close()
await pgvector_session_manager.close()
await pool.__aexit__(None, None, None)